In [0]:
#mounting azure storage to databricks
dbutils.fs.mount(

  source = "wasbs://cs4raw@casestudy4.blob.core.windows.net",

  mount_point = "/mnt/cs4raw",

    extra_configs = {'fs.azure.sas.' + 'cs4raw' + '.' + 'casestudy4' + '.blob.core.windows.net': '?sp=r&st=2023-10-05T15:13:46Z&se=2023-10-06T11:13:46Z&spr=https&sv=2022-11-02&sr=c&sig=rsSANB41O9%2BJgaO9coCLhy5Rc7tRhA8U78jsnTWG188%3D'})

---------------------------------------------------------------------------
ExecutionError                            Traceback (most recent call last)
File <command-3985337521885858>, line 2
      1 #mounting azure storage to databricks
----> 2 dbutils.fs.mount(
      3 
      4   source = "wasbs://cs4raw@casestudy4.blob.core.windows.net",
      5 
      6   mount_point = "/mnt/cs4raw",
      7 
      8     extra_configs = {'fs.azure.sas.' + 'cs4raw' + '.' + 'casestudy4' + '.blob.core.windows.net': '?sp=r&st=2023-10-05T15:13:46Z&se=2023-10-06T11:13:46Z&spr=https&sv=2022-11-02&sr=c&sig=rsSANB41O9%2BJgaO9coCLhy5Rc7tRhA8U78jsnTWG188%3D'})

File /databricks/python_shell/dbruntime/dbutils.py:362, in DBUtils.FSHandler.prettify_exception_message.<locals>.f_with_exception_handling(*args, **kwargs)
    360 exc.__context__ = None
    361 exc.__cause__ = None
--> 362 raise exc

ExecutionError: An error occurred while calling o449.mount.
: java.rmi.RemoteException: java.lang.IllegalArgumentExcept

In [0]:
output_container_name = 'cs4raw'
storage_name = 'casestudy4'
sas_key = 'sp=r&st=2023-10-05T15:13:46Z&se=2023-10-06T11:13:46Z&spr=https&sv=2022-11-02&sr=c&sig=rsSANB41O9%2BJgaO9coCLhy5Rc7tRhA8U78jsnTWG188%3D'

spark.conf.set(
  "fs.azure.account.key.%s.blob.core.windows.net" % storage_name,
  sas_key)

output_container_path = "wasbs://%s@%s.blob.core.windows.net" % (output_container_name, storage_name)
output_blob_folder = output_container_path

In [0]:

from azure.storage.blob import (
    BlockBlobService
)
import io
accountName = storage_name
accountKey = sas_key
containerName = output_container_name
blobName = "output.csv"
blobService = BlockBlobService(account_name=accountName, account_key=accountKey)
output = io.StringIO().df.to_csv (index_label="idx", encoding = "utf-8")
blobService.create_blob_from_text(containerName, blobName,output)


---------------------------------------------------------------------------
AttributeError                            Traceback (most recent call last)
File <command-1902721722671825>, line 1
----> 1 dbutils.library.installPyPI("azure.storage.blob")
      2 from azure.storage.blob import (
      3     BlockBlobService
      4 )
      5 import io

AttributeError: 'LibraryHandler' object has no attribute 'installPyPI'

In [0]:
dbutils.fs.cp("dbfs:/mnt/cs4raw/output", "abfss://cs4raw@casestudy4.dfs.core.windows.net/finalOutput")

---------------------------------------------------------------------------
ExecutionError                            Traceback (most recent call last)
File <command-1902721722671827>, line 1
----> 1 dbutils.fs.cp("dbfs:/mnt/cs4raw/output", "abfss://cs4raw@casestudy4.dfs.core.windows.net/finalOutput")

File /databricks/python_shell/dbruntime/dbutils.py:362, in DBUtils.FSHandler.prettify_exception_message.<locals>.f_with_exception_handling(*args, **kwargs)
    360 exc.__context__ = None
    361 exc.__cause__ = None
--> 362 raise exc

ExecutionError: An error occurred while calling o445.cp.
: shaded.databricks.org.apache.hadoop.fs.azure.AzureException: java.util.NoSuchElementException: An error occurred while enumerating the result, check the original exception for details.
	at shaded.databricks.org.apache.hadoop.fs.azure.AzureNativeFileSystemStore.retrieveMetadata(AzureNativeFileSystemStore.java:2347)
	at shaded.databricks.org.apache.hadoop.fs.azure.NativeAzureFileSystem.getFileStatus(N

In [0]:
#importing all functions and types
from pyspark.sql.functions import *
from pyspark.sql.types import *

In [0]:
def readFile(fileName):
    return  spark.read.csv(f"dbfs:/mnt/cs4raw/{fileName}.csv",inferSchema=True, header=True)

In [0]:
def convertToIntEconomics(dataframe):
    for pres_col in dataframe.dtypes:
        col_name=pres_col[0]
        if( col_name.split(" ")[0]=="Economics"):
            dataframe = dataframe.withColumn(col_name,col(col_name).cast('double').cast(DecimalType(18,8)))
            dataframe=dataframe.na.fill(value=0,subset=[col_name])
    return dataframe


In [0]:
def removeNulls(dataframe):  
    for col in dataframe.dtypes:
        col_name=col[0]
        col_type=col[1]
        if col_name == "_c0":
            dataframe=dataframe.drop(col_name)
        elif col_type =="int" or col_type == "double" or col_type == "float":
            dataframe=dataframe.na.fill(value=0,subset=[col_name])
        elif col_type == "string":
            dataframe=dataframe.na.fill(value="",subset=[col_name])
    return dataframe

In [0]:
#Reading all the files
df_Asset = readFile("ASSET")
df_Production=readFile("PRODUCTION")
df_OilAndGas=readFile("OILANDGAS")
df_Npv=readFile("NPV")
df_Geagraphy = readFile("GEOGRAPHY")
df_BreakEvenPrices=readFile("BREAKEVENPRICES")
df_Economics=readFile("ECONOMICS")
df_EconomicsType=readFile("ECONOMICSTYPE")




wasbs://cs4raw@casestudy4.blob.core.windows.net


---------------------------------------------------------------------------
Py4JJavaError                             Traceback (most recent call last)
File <command-3985337521885866>, line 18
      9 df_EconomicsType=readFile("ECONOMICSTYPE")
     11 print(output_blob_folder)
     12 (df_Asset
     13  .coalesce(1)
     14  .write
     15  .mode("overwrite")
     16  .option("header", "true")
     17  .format("com.databricks.spark.csv")
---> 18  .save("wasbs://cs4raw@casestudy4.blob.core.windows.net"))

File /databricks/spark/python/pyspark/instrumentation_utils.py:48, in _wrap_function.<locals>.wrapper(*args, **kwargs)
     46 start = time.perf_counter()
     47 try:
---> 48     res = func(*args, **kwargs)
     49     logger.log_success(
     50         module_name, class_name, function_name, time.perf_counter() - start, signature
     51     )
     52     return res

File /databricks/spark/python/pyspark/sql/readwriter.py:1463, in DataFrameWriter.save(self, path, format, mode, parti

In [0]:
#Removing nulls from all files
df_Asset = removeNulls(df_Asset)
df_Production=removeNulls(df_Production)
df_OilAndGas=removeNulls(df_OilAndGas)
df_Npv=removeNulls(df_Npv)
df_Geagraphy = removeNulls(df_Geagraphy)
df_BreakEvenPrices=removeNulls(df_BreakEvenPrices)
df_Economics=removeNulls(df_Economics)
df_EconomicsType=removeNulls(df_EconomicsType)


In [0]:
df_Asset.display()

In [0]:
df_Economics = convertToIntEconomics(df_Economics)
df_Economics.display()

Id FK_Asset Year FK_OtherParameter FK_OilAndGas FK_HistoricCompany FK_LifeCycleTS FK_LifeCycle FK_Company FK_EconomicsType FK_DataQuality FK_OilAndGasType Economics Forward Case Economics High Case Economics Low Case Economics Mid Case Economics Economics Low Low Case Economics Mid Low Case Economics Low Low Low Case Economics Mid Low Low Case Economics Mid Mid Low Case Economics Mid Mid Low Low Case 57814893 194792 2057 120 2 10 2 24 10 8 30 10 -0.01650000 0E-8 0E-8 0E-8 0E-8 0E-8 -0.01650000 0E-8 0E-8 -0.01660000 0E-8 57814894 194792 2048 12 4 10 14 24 10 8 30 11 0.15600000 0.10000000 0.03180000 0.17000000 -0.04690000 0.00800000 0.09240000 -0.01130000 0.05210000 0.13300000 0.07220000 57814895 194792 2057 12 9 685 2 24 685 1 30 15 0.00390000 0E-8 0E-8 0E-8 0E-8 0E-8 0.00390000 0E-8 0E-8 0.00390000 0E-8 57814896 194792 1976 6 12 6 24 24 685 3 30 8 0.00030000 0.00030000 0.00030000 0.00030000 0.00030000 0.00030000 0.00030000 0.00030000 0.00030000 0.00030000 0.00030000 57814919 194792 2044 120 2 168 17 24 168 6 30 10 -0.06860000 0E-8 -0.04660000 0E-8 -0.04230000 -0.03660000 -0.07670000 -0.02660000 -0.04230000 -0.08670000 -0.04870000 57814951 194792 2049 12 9 10 14 24 10 6 30 15 0.00140000 0.00300000 0.00080000 0.00240000 0.00110000 0.00060000 0.00160000 0.00030000 0.00110000 0.00190000 0.00140000 57814984 194792 2053 12 9 168 2 24 168 11 30 15 0.00010000 0.00010000 0E-8 0.00010000 0E-8 0E-8 0.00010000 0E-8 0E-8 0.00010000 0E-8 57815004 194792 2047 12 9 168 16 24 168 9 30 15 0.00050000 0.00060000 0.00050000 0.00060000 0.00050000 0.00050000 0.00050000 0.00050000 0.00050000 0.00050000 0.00050000 57815011 194792 2060 120 9 685 1 24 685 8 30 15 0E-8 0E-8 0E-8 0E-8 0E-8 0E-8 0E-8 0E-8 0E-8 0E-8 0E-8 57814932 194792 2000 12 12 3 24 24 685 6 30 8 -0.00290000 -0.00290000 -0.00290000 -0.00290000 -0.00290000 -0.00290000 -0.00290000 -0.00290000 -0.00290000 -0.00290000 -0.00290000 57814961 194792 2047 12 2 10 16 24 10 6 30 10 0.06390000 0.09480000 0.05570000 0.08290000 0.05950000 0.05190000 0.06700000 0.04810000 0.05940000 0.07100000 0.06320000 57814933 194792 2048 12 9 168 14 24 168 13 30 15 0.00010000 0.00010000 0.00010000 0.00010000 0.00010000 0.00010000 0.00010000 0.00010000 0.00010000 0.00010000 0.00010000 57814935 194792 1989 6 12 6 24 24 685 3 30 8 0.00030000 0.00030000 0.00030000 0.00030000 0.00030000 0.00030000 0.00030000 0.00030000 0.00030000 0.00030000 0.00030000 57814989 194792 2052 12 4 685 14 24 685 9 30 11 0.00350000 0.00380000 0.00350000 0.00360000 0.11300000 0.00350000 0.00350000 0.11300000 0.00350000 0.11600000 0.00350000 57816021 194792 1993 6 12 20932 24 24 685 3 30 8 0.00090000 0.00090000 0.00090000 0.00090000 0.00090000 0.00090000 0.00090000 0.00090000 0.00090000 0.00090000 0.00090000 57816024 194792 2059 12 9 10 1 24 10 6 30 15 0E-8 -0.00410000 0E-8 0E-8 0E-8 0E-8 0E-8 0E-8 0E-8 0E-8 0E-8 57816048 194792 2046 12 2 685 16 24 685 11 30 10 0.00080000 0.00080000 0.00080000 0.00080000 0.00080000 0.00080000 0.00080000 0.00080000 0.00080000 0.00080000 0.00080000 57815070 194792 1981 12 12 20932 24 24 685 6 30 8 -0.00090000 -0.00090000 -0.00090000 -0.00090000 -0.00090000 -0.00090000 -0.00090000 -0.00090000 -0.00090000 -0.00090000 -0.00090000 57812362 194791 2042 12 4 685 23 24 685 11 30 11 0.00100000 0.00100000 0.00100000 0.00100000 0.00100000 0.00100000 0.00100000 0.00100000 0.00100000 0.00100000 0.00100000 57816084 194792 2042 12 12 10 23 24 10 13 30 8 0E-8 0E-8 0E-8 0E-8 0E-8 0E-8 0E-8 0E-8 0E-8 0E-8 0E-8 52936839 122542 2032 120 4 12830 16 31 12830 9 30 11 -0.27700001 0E-8 -0.27700001 0E-8 -0.27700001 -0.27700001 -0.27700001 -0.27700001 -0.27700001 0E-8 -0.27700001 57815042 194792 1968 6 12 3 24 24 168 3 30 8 0.00420000 0.00420000 0.00420000 0.00420000 0.00420000 0.00420000 0.00420000 0.00420000 0.00420000 0.00420000 0.00420000 57815078 194792 1962 6 12 20932 24 24 685 3 30 8 0.00090000 0.00090000 0.00090000 0.00090000 0.00090000 0.00090000 0.00090000 0.00090000 0.00090000 0.00090000 0.00090000 57812343 194791 2052 12 4 685

###Questions

In [0]:
df_Asset=df_Asset.withColumnRenamed("Id","AssetId")
df_Production=df_Production.withColumnRenamed("Id","ProductionId")
df_OilAndGas=df_OilAndGas.withColumnRenamed("Id","OilAndGasId")
df_Economics=df_Economics.withColumnRenamed("Id","EconomicsId")
df_Geagraphy=df_Geagraphy.withColumnRenamed("Id","GeographyId")
df_BreakEvenPrices=df_BreakEvenPrices.withColumnRenamed("Id","BreakEvenPricesId")
df_Npv=df_Npv.withColumnRenamed("Id","NpvId")
df_EconomicsType=df_EconomicsType.withColumnRenamed("Id","EconomicsTypeId")

##Q1

In [0]:
df_Ass_Pro = df_Asset.join(df_Production,df_Asset.AssetId==df_Production.FK_Asset,'inner')

In [0]:
df_Ass_Pro_Oil = df_Ass_Pro.join(df_OilAndGas,df_OilAndGas.OilAndGasId==df_Ass_Pro.FK_OilAndGas,'inner')

In [0]:
q1 = df_Ass_Pro_Oil.filter(col("Oil And Gas Category")=="Oil")

In [0]:
q1.write.mode("overwrite").format("delta").option("delta.columnMapping.mode", "name").saveAsTable("table1")

In [0]:
%sql
select sum(Production) from table1

sum(Production) 2811.602899058

##Q2

In [0]:
df_Npv.printSchema()

root
 |-- NpvId: integer (nullable = true)
 |-- Fk_Asset: integer (nullable = true)
 |-- FK_OtherParameter: integer (nullable = true)
 |-- FK_Company: integer (nullable = true)
 |-- FK_OilAndGas: integer (nullable = true)
 |-- FK_HistoricCompany: integer (nullable = true)
 |-- FK_DataQuality: integer (nullable = true)
 |-- FK_LifeCycleTS: integer (nullable = true)
 |-- FK_LifeCycle: integer (nullable = true)
 |-- FK_OilAndGasType: integer (nullable = true)
 |-- NPV Current Year Forward Case: double (nullable = false)
 |-- NPV Current Year High Case: double (nullable = false)
 |-- NPV Current Year Low Case: double (nullable = false)
 |-- NPV Current Year: double (nullable = false)
 |-- NPV Current Year Mid Case: double (nullable = false)
 |-- NPV Current Year Low Low Case: double (nullable = false)
 |-- NPV Current Year Mid Low Case: double (nullable = false)
 |-- NPV Current Year Low Low Low Case: double (nullable = false)
 |-- NPV Current Year Mid Low Low Case: double (nullable = fals

In [0]:
df_Ass_Npv = df_Asset.join(df_Npv,df_Npv.Fk_Asset==df_Asset.AssetId,'inner').groupBy('Field Type Category').sum('NPV Current Year')

In [0]:
df_Ass_Npv.display()

Field Type Category sum(NPV Current Year) Gas-Condensate field 3116.0390205270005 Oil field 2342.3992721829986

In [0]:
df_Ass_Npv.write.mode("overwrite").format("delta").option("delta.columnMapping.mode", "name").saveAsTable("table2")

In [0]:
%sql
select * from table2

Field Type Category sum(NPV Current Year) Gas-Condensate field 3116.0390205270005 Oil field 2342.3992721829986

##Q4

In [0]:
df_Production_filterd = df_Production.filter("Year between 2024 and 2033")

In [0]:
df_OilAndGas_filtered = df_OilAndGas.filter(col("Oil And Gas Category")=="Oil")

In [0]:
df_Prod_Oil_filtered=df_OilAndGas_filtered.join(df_Production_filterd, df_Production_filterd.FK_OilAndGas==df_OilAndGas_filtered.OilAndGasId,'inner')

In [0]:
df_Prod_Oil_filtered_Grp = df_Prod_Oil_filtered.groupBy("Year").sum("Production").sort("Year")

In [0]:
df_Prod_Oil_filtered_Grp.display()

Year sum(Production) 2024 20.275399978 2025 18.649799967 2026 18.72039989 2027 19.313999877000004 2028 18.5788999 2029 17.358799958 2030 14.460299950999998 2031 12.374000052999994 2032 10.724499879000001 2033 10.023699861

In [0]:
df_Prod_Oil_filtered_Grp.write.mode("overwrite").format("delta").option("delta.columnMapping.mode", "name").saveAsTable("table4")

In [0]:
%sql
select * from table4

Year sum(Production) 2024 20.275399978 2025 18.649799967 2026 18.72039989 2027 19.313999877000004 2028 18.5788999 2029 17.358799958 2030 14.460299950999998 2031 12.374000052999994 2032 10.724499879000001 2033 10.023699861

##Q3

In [0]:
Economics_Category_list = ['Well Capex','Exploration Capex','Facility Capex']
df_EconomicsType_filtered = df_EconomicsType.filter(col('Economics Category').isin(Economics_Category_list))
df_EconomicsType_filtered.display()

EconomicsTypeId Economics Group Economics Category 3 Exploration Capex Exploration Capex 4 Capex Facility Capex 14 Capex Well Capex

In [0]:
df_Ass_Geo = df_Asset.join(df_Geagraphy, df_Geagraphy.GeographyId==df_Asset.Fk_Geography,'inner')

In [0]:
df_Ass_Geo_Eco = df_Ass_Geo.join(df_Economics,df_Economics.FK_Asset == df_Ass_Geo.AssetId,'inner')

In [0]:
df_Ass_Geo_Eco_Ecot = df_Ass_Geo_Eco.join(df_EconomicsType_filtered,df_EconomicsType_filtered.EconomicsTypeId == df_Ass_Geo_Eco.FK_EconomicsType,'inner')

In [0]:
df_Ass_Geo_Eco_Ecot = df_Ass_Geo_Eco_Ecot.filter("Year = 2023")

In [0]:
df_Ass_Geo_Eco_Ecot = df_Ass_Geo_Eco_Ecot.groupBy("Location").sum("Economics").sort("sum(Economics)")

In [0]:
df_Ass_Geo_Eco_Ecot.write.mode("overwrite").format("delta").option("delta.columnMapping.mode", "name").saveAsTable("table3")

In [0]:
%sql
select * from table3

Location sum(Economics) 06/95 (Siri), DK 0E-8 Gert (5603/27, 28), DK 0.02040000 Svend (5504/25), DK 0.02440000 04/98 (Svane 1A), DK 0.02480000 Rolf (5504/10, 14), DK 0.02510000 01/6, DK 0.04440000 07/89, DK 0.04800000 SouthWest Area (Harald), DK 0.05810000 4/16, DK 0.06300000 12/6, DK 0.09430000 8/06 Area B, DK 0.09670000 9/16, DK 0.17280000 05/6, DK 0.36600000 05/98 (Hejre), DK 0.37000000 03/09, DK 0.61940000 2/16, DK 0.96379997 16/98 (Cecilie), DK 1.96349995 04/95 (Nini), DK 3.06340002 Tyra South East, DK 28.79790015 07/89 (Arne South), DK 46.76600122 Contiguous Area (Dan), DK 326.42710263

In [0]:
df_Asset.write.csv("dbfs:/mnt/cs4staged")